In [1]:
!pip install grpcio==1.42.0 tensorflow-serving-api==2.8.0

     ---------------------------------------- 0.0/3.3 MB ? eta -:--:--
      --------------------------------------- 0.0/3.3 MB 991.0 kB/s eta 0:00:04
     - -------------------------------------- 0.1/3.3 MB 1.3 MB/s eta 0:00:03
     -- ------------------------------------- 0.2/3.3 MB 1.5 MB/s eta 0:00:03
     ----- ---------------------------------- 0.4/3.3 MB 2.2 MB/s eta 0:00:02
     -------- ------------------------------- 0.7/3.3 MB 3.0 MB/s eta 0:00:01
     ------------- -------------------------- 1.1/3.3 MB 3.8 MB/s eta 0:00:01
     ---------------- ----------------------- 1.4/3.3 MB 4.1 MB/s eta 0:00:01
     -------------------- ------------------- 1.7/3.3 MB 4.5 MB/s eta 0:00:01
     ------------------------ --------------- 2.0/3.3 MB 4.6 MB/s eta 0:00:01
     ---------------------------- ----------- 2.3/3.3 MB 4.7 MB/s eta 0:00:01
     ------------------------------- -------- 2.6/3.3 MB 4.9 MB/s eta 0:00:01
     ----------------------------------- ---- 2.9/3.3 MB 5.0 MB/s eta

In [2]:
!pip install keras-image-helper

  Using cached keras_image_helper-0.0.1-py3-none-any.whl (4.6 kB)


In [5]:
import grpc

import tensorflow as tf

from tensorflow_serving.apis import predict_pb2
from tensorflow_serving.apis import prediction_service_pb2_grpc

In [6]:
host = 'localhost:8500'

channel = grpc.insecure_channel(host)

stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)

In [8]:
from keras_image_helper import create_preprocessor

In [10]:
preprocessor = create_preprocessor('xception', target_size=(299, 299))

In [11]:
url = 'http://bit.ly/mlbookcamp-pants'
X = preprocessor.from_url(url)

In [12]:
X 

array([[[[-0.11372548, -0.15294117, -0.19999999],
         [-0.11372548, -0.15294117, -0.19999999],
         [-0.10588235, -0.14509803, -0.19215685],
         ...,
         [-0.01960784, -0.01960784, -0.08235294],
         [-0.04313725, -0.04313725, -0.10588235],
         [-0.11372548, -0.11372548, -0.17647058]],

        [[-0.09019607, -0.12941176, -0.17647058],
         [-0.09019607, -0.12941176, -0.17647058],
         [-0.08235294, -0.12156862, -0.16862744],
         ...,
         [-0.01960784, -0.01960784, -0.08235294],
         [-0.04313725, -0.04313725, -0.10588235],
         [-0.10588235, -0.10588235, -0.16862744]],

        [[-0.09803921, -0.1372549 , -0.18431371],
         [-0.09803921, -0.1372549 , -0.18431371],
         [-0.09019607, -0.12941176, -0.17647058],
         ...,
         [-0.01960784, -0.01960784, -0.08235294],
         [-0.03529412, -0.03529412, -0.09803921],
         [-0.09019607, -0.09019607, -0.15294117]],

        ...,

        [[-0.67058825, -0.7019608 , -0

In [13]:
def np_to_proto(data):
    return tf.make_tensor_proto(data, shape=data.shape)

In [15]:
np_to_proto(X)

dtype: DT_FLOAT
tensor_shape {
  dim {
    size: 1
  }
  dim {
    size: 299
  }
  dim {
    size: 299
  }
  dim {
    size: 3
  }
}
tensor_content: "\350\350\350\275\234\234\034\276\314\314L\276\350\350\350\275\234\234\034\276\314\314L\276\330\330\330\275\224\224\024\276\304\304D\276\270\270\270\275\204\204\004\276\264\2644\276\210\210\210\275\330\330\330\275\234\234\034\276\360\360p\275\310\310\310\275\224\224\024\276\260\2600\275\250\250\250\275\204\204\004\276\240\240\240\274\360\360p\275\330\330\330\275\300\300@\274\320\320P\275\310\310\310\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\360\360p\275\300\2600=\000\201\200;\240\240\240\274\220\210\210=\000\341\340<\000\201\200;\260\250\250=\300\2600=\300\240\240<\340\330\330=\220\210\210=\300\2600=\360\350\350=\240\230\230=\340\320P=\220\214\014>\320\310\310=\240\230\230=\000\371\370=\260\250\250=\000\361p=\220\21

In [16]:
pb_request = predict_pb2.PredictRequest()

pb_request.model_spec.name = 'clothing-model'
pb_request.model_spec.signature_name = 'serving_default'

pb_request.inputs['input_16'].CopyFrom(np_to_proto(X))

In [21]:
pb_response = stub.Predict(pb_request, timeout=20.0)

In [25]:
preds = pb_response.outputs['dense_13'].float_val

In [24]:
classes = ['dress',
 'hat',
 'longsleeve',
 'outwear',
 'pants',
 'shirt',
 'shoes',
 'shorts',
 'skirt',
 't-shirt']

In [27]:
dict(zip(classes, preds))

{'dress': -1.7805181741714478,
 'hat': -3.757965326309204,
 'longsleeve': -2.626631021499634,
 'outwear': -0.6393223404884338,
 'pants': 8.415915489196777,
 'shirt': -1.7304704189300537,
 'shoes': -4.369088649749756,
 'shorts': 2.122248888015747,
 'skirt': -2.054950475692749,
 't-shirt': -4.2383713722229}